# IBM Applied Data Science Capstone Course by Coursera

### Opening a New Shopping Mall in Auckland, New Zealand

   -  Build a dataframe of neighborhoods in Auckland, New Zealand by web scraping the data from Wikipedia page
   -  Get the geographical coordinates of the neighborhoods
   -  Obtain the venue data for the neighborhoods from Foursquare API
   -  Explore and cluster the neighborhoods
   -  Select the best cluster to open a new shopping mall

### 1. Import Libraries

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans
!conda install -c anaconda xlrd --yes
!conda install -c conda-forge folium=0.5.0 --yes

import folium # map rendering library

print("Libraries imported.")


Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - xlrd


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    xlrd-1.2.0                 |             py_0         108 KB  anaconda
    openssl-1.1.1g             |       h7b6447c_0         3.8 MB  anaconda
    ca-certificates-2020.1.1   |                0         132 KB  anaconda
    certifi-2020.4.5.1         |           py36_0         159 KB  anaconda
    ------------------------------------------------------------
                                           Total:         4.2 MB

The following packages will be UPDATED:

    ca-certificates: 2020.1.1-0        --> 2020.1.1-0        anaconda
    certifi:         2020.4.5.1-py36_0 --> 2020.4.5.1-py36_0 anaconda
    openssl:         1.1.1f-h7b6447c_0 --> 1.1.1g-h7b6447c_0 anaconda
    xlrd:            1.2.0-py_0       

In [3]:
!pip install geocoder
import geocoder # to get coordinates

     |████████████████████████████████| 102kB 5.4MB/s ta 0:00:011


### 2. Scrap data from Wikipedia page into a DataFrame

In [4]:
# send the GET request
data1 = requests.get("https://en.wikipedia.org/wiki/List_of_suburbs_of_Auckland").text

In [5]:
# parse data from the html into a beautifulsoup object
soup = BeautifulSoup(data1, 'html.parser')

In [6]:
# create a list to store neighborhood data
neighborhoodList = []

In [7]:
# append the data into the list
for row in soup.find_all("div", class_="div-col columns column-width")[0].findAll("li"):
    neighborhoodList.append(row.text)
for row in soup.find_all("div", class_="div-col columns column-width")[1].findAll("li"):
    neighborhoodList.append(row.text)
for row in soup.find_all("div", class_="div-col columns column-width")[2].findAll("li"):
    neighborhoodList.append(row.text)
for row in soup.find_all("div", class_="div-col columns column-width")[3].findAll("li"):
    neighborhoodList.append(row.text)
for row in soup.find_all("div", class_="div-col columns column-width")[4].findAll("li"):
    neighborhoodList.append(row.text)
for row in soup.find_all("div", class_="div-col columns column-width")[5].findAll("li"):
    neighborhoodList.append(row.text)
for row in soup.find_all("div", class_="div-col columns column-width")[6].findAll("li"):
    neighborhoodList.append(row.text)   

In [8]:
ak_df = pd.DataFrame({"Neighborhood": neighborhoodList})
ak_df.head()

Neighborhood
0     Arch Hill
1  Auckland CBD
2      Avondale
3      Balmoral
4     Blackpool

In [9]:
ak_df.shape

(302, 1)

### 3. Get the geographical coordinates

In [10]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Auckland, New Zealand'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [11]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in ak_df["Neighborhood"].tolist() ]

In [12]:
coords

[[-36.86301999999995, 174.74858000000006],
 [-36.84839904099994, 174.76438785300002],
 [-36.89044821899995, 174.6870174820001],
 [-36.88819999999998, 174.7401900000001],
 [-37.05156439523053, 174.88439705033372],
 [-36.92819999999995, 174.70019000000002],
 [-36.86413508299995, 174.75743271800002],
 [-36.86956533042306, 174.77598845331576],
 [-36.896377420999954, 174.81373710200012],
 [-36.88845407399998, 174.77293816600002],
 [-36.85287929799995, 174.75035326400007],
 [-36.86036095299994, 174.87265930000012],
 [-36.87394120099998, 174.86095625600012],
 [-36.85329999999993, 174.77975000000004],
 [-36.89491322499998, 174.79262520600003],
 [-36.92865648363817, 174.64980099283827],
 [-36.861568621999936, 174.73955514300008],
 [-36.83819999999997, 174.72019000000012],
 [-36.92389779599995, 174.75536291900005],
 [-36.87019698199998, 174.7452094570001],
 [-36.85725985999994, 174.84097833500005],
 [-36.93035918099997, 174.71985815800008],
 [-36.86950058399998, 174.82957281000006],
 [-36.838199

In [13]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [14]:
# merge the coordinates into the original dataframe
ak_df['Latitude'] = df_coords['Latitude']
ak_df['Longitude'] = df_coords['Longitude']

In [15]:
# check the neighborhoods and the coordinates
print(ak_df.shape)
ak_df.head()

(302, 3)


Neighborhood   Latitude   Longitude
0     Arch Hill -36.863020  174.748580
1  Auckland CBD -36.848399  174.764388
2      Avondale -36.890448  174.687017
3      Balmoral -36.888200  174.740190
4     Blackpool -37.051564  174.884397

In [16]:
# save the DataFrame as CSV file
ak_df.to_csv("ak_df1.csv", index=False)

In [17]:
# get the coordinates of Auckland 
address = 'Auckland, New Zealand'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Auckland, New Zealand {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Auckland, New Zealand -36.852095, 174.7631803.


### 4. Create a map of Auckland with neighborhoods superimposed on top

In [18]:
 #create map of Auckland using latitude and longitude values
map_ak = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(ak_df['Latitude'], ak_df['Longitude'], ak_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_ak)  
    
map_ak

In [19]:
# save the map as HTML file
map_ak.save('map_ak1.html')

### 5. Use the Foursquare API to explore the neighborhoods

In [20]:
# define Foursquare Credentials and Version
CLIENT_ID = '0C0JMQFC2TQFMVH5EKG2WSJFQIBGLXHMNFCQK0BMDEYGT2IH' # your Foursquare ID
CLIENT_SECRET = 'EVR4243KZWWZE5DT52XLLDCKQIZKB4K311AV5I3A2J32NKSL' # your Foursquare Secret
VERSION = '20200605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)


Your credentails:
CLIENT_ID: 0C0JMQFC2TQFMVH5EKG2WSJFQIBGLXHMNFCQK0BMDEYGT2IH
CLIENT_SECRET:EVR4243KZWWZE5DT52XLLDCKQIZKB4K311AV5I3A2J32NKSL


#### Now, let's get the top 100 venues, within a radius of 2000 meters.

In [21]:
radius = 2000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(ak_df['Latitude'], ak_df['Longitude'], ak_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
   # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
       
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))


In [22]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()

(11005, 7)


Neighborhood  Latitude  Longitude                   VenueName  \
0    Arch Hill -36.86302  174.74858              Grey Lynn Park   
1    Arch Hill -36.86302  174.74858                   Countdown   
2    Arch Hill -36.86302  174.74858            Ponsonby Central   
3    Arch Hill -36.86302  174.74858         El Sizzling Chorizo   
4    Arch Hill -36.86302  174.74858  Viva Latino! Dance Studios   

   VenueLatitude  VenueLongitude           VenueCategory  
0     -36.861524      174.743148                    Park  
1     -36.858375      174.748862                  Market  
2     -36.856276      174.746169           Shopping Mall  
3     -36.856290      174.746131  Argentinian Restaurant  
4     -36.860666      174.753579            Dance Studio

#### Let's check how many venues were returned for each neighorhood

In [23]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                          
Airport Oaks                 7          7          7              7   
Albany                      66         66         66             66   
Alfriston                    2          2          2              2   
Algies Bay                 100        100        100            100   
Anawhata                     4          4          4              4   
Ararimu                    100        100        100            100   
Arch Hill                  100        100        100            100   
Ardmore                    100        100        100            100   
Arkles Bay                  16         16         16             16   
Army Bay                     6          6          6              6   
Auckland CBD               100        100        100            100   
Avondale                    37         37         37             37   
Awhitu                     100        100        100            100   
Balmoral                   100        100        100            100   
Bayswater                   18         18         18             18   
Bayview                     12         12         12             12   
Beach Haven                 18         18         18             18   
Beachlands                   5          5          5              5   
Belmont                     13         13         13             13   
Bethells Beach               1          1          1              1   
Big Omaha                  100        100        100            100   
Birkdale                    27         27         27             27   
Birkenhead                  44         44         44             44   
Blackpool                    6          6          6              6   
Blockhouse Bay              16         16         16             16   
Bombay                     100        100        100            100   
Botany Downs                28         28         28             28   
Browns Bay                  36         36         36             36   
Buckland                    13         13         13             13   
Bucklands Beach              6          6          6              6   
Burswood                    49         49         49             49   
Campbells Bay               28         28         28             28   
Castor Bay                  21         21         21             21   
Chapel Downs                49         49         49             49   
Chatswood                   39         39         39             39   
Cheltenham                  45         45         45             45   
Clarks Beach                 7          7          7              7   
Clendon Park                 4          4          4              4   
Clevedon                   100        100        100            100   
Clover Park                 37         37         37             37   
Cockle Bay                  18         18         18             18   
Conifer Grove                8          8          8              8   
Cornwallis                   4          4          4              4   
Crown Hill                  41         41         41             41   
Dairy Flat                  63         63         63             63   
Dannemora                   42         42         42             42   
Devonport                   44         44         44             44   
Dome Forest                  3          3          3              3   
Dome Valley                100        100        100            100   
Drury                       44         44         44             44   
East Tamaki                 24         24         24             24   
East Tamaki Heights         28         28         28             28   
Eastern Beach               13         13         13             13   
Eden Terrace               100        100        100            100   
Eden Valley                100        100     

#### Let's find out how many unique categories can be curated from all the returned venues

In [24]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 255 uniques categories.


In [25]:
# print out the list of categories
venues_df['VenueCategory'].unique()[:50]

array(['Park', 'Market', 'Shopping Mall', 'Argentinian Restaurant',
       'Dance Studio', 'Gym / Fitness Center', 'Café', 'Pizza Place',
       'Italian Restaurant', 'Bistro', 'Burger Joint',
       'Fruit & Vegetable Store', 'Food Court', 'South Indian Restaurant',
       'Japanese Restaurant', 'French Restaurant', 'Toy / Game Store',
       'Sushi Restaurant', 'Vietnamese Restaurant',
       'Vegetarian / Vegan Restaurant', 'Bakery', 'American Restaurant',
       'General Entertainment', 'Restaurant', 'Mexican Restaurant',
       'Noodle House', 'Malay Restaurant', 'Food Truck', 'Tattoo Parlor',
       'Middle Eastern Restaurant', 'Stadium', 'Gourmet Shop',
       'Food & Drink Shop', 'Record Shop', 'Chinese Restaurant',
       'Coffee Shop', 'Bar', 'Bagel Shop', 'Indian Restaurant',
       'Yakitori Restaurant', 'Hotel', 'Gym', 'Pub', 'Cupcake Shop',
       'Gay Bar', 'Thai Restaurant', 'City Hall', 'Dessert Shop',
       'Theater', 'Cocktail Bar'], dtype=object)

In [26]:
# check if the results contain "Shopping Mall"
"Neighborhood" in venues_df['VenueCategory'].unique()

True

### 6. Analyze Each Neighborhood

In [27]:
# one hot encoding
ak_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ak_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ak_onehot.columns[-1]] + list(ak_onehot.columns[:-1])
ak_onehot = ak_onehot[fixed_columns]

print(ak_onehot.shape)
ak_onehot.head()

(11005, 256)


Neighborhoods  African Restaurant  Airport  Airport Terminal  \
0     Arch Hill                   0        0                 0   
1     Arch Hill                   0        0                 0   
2     Arch Hill                   0        0                 0   
3     Arch Hill                   0        0                 0   
4     Arch Hill                   0        0                 0   

   American Restaurant  Antique Shop  Aquarium  Arcade  \
0                    0             0         0       0   
1                    0             0         0       0   
2                    0             0         0       0   
3                    0             0         0       0   
4                    0             0         0       0   

   Argentinian Restaurant  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0                       0            0                    0                 0   
1                       0            0                    0                 0   
2                       0            0                    0                 0   
3                       1            0                    0                 0   
4                       0            0                    0                 0   

   Athletics & Sports  Auditorium  Automotive Shop  BBQ Joint  \
0                   0           0                0          0   
1                   0           0                0          0   
2                   0           0                0          0   
3                   0           0                0          0   
4                   0           0                0          0   

   Badminton Court  Bagel Shop  Bakery  Bar  Baseball Field  Basketball Court  \
0                0           0       0    0               0                 0   
1                0           0       0    0               0                 0   
2                0           0       0    0               0                 0   
3                0           0       0    0               0                 0   
4                0           0       0    0               0                 0   

   Basketball Stadium  Bay  Beach  Bed & Breakfast  Beer Bar  Beer Garden  \
0                   0    0      0                0         0            0   
1                   0    0      0                0         0            0   
2                   0    0      0                0         0            0   
3                   0    0      0                0         0            0   
4                   0    0      0                0         0            0   

   Big Box Store  Bike Shop  Bike Trail  Bistro  Boat or Ferry  Bookstore  \
0              0          0           0       0              0          0   
1              0          0           0       0              0          0   
2              0          0           0       0              0          0   
3              0          0           0       0              0          0   
4              0          0           0       0              0          0   

   Boutique  Bowling Alley  Bowling Green  Brazilian Restaurant  \
0         0              0              0                     0   
1         0              0              0                     0   
2         0              0              0                     0   
3         0              0              0                     0   
4         0              0              0                     0   

   Breakfast Spot  Brewery  Bubble Tea Shop  Buffet  Burger Joint  \
0               0        0                0       0             0   
1               0        0                0       0             0   
2               0        0                0       0             0   
3               0        0                0       0             0   
4               0        0                0       0             0   

   Bus Station  Business Service  Cafeteria  Café  Cajun / Creole Restaurant  \
0            0                 0          0     0                  

In [29]:
ak_grouped = ak_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(ak_grouped.shape)
ak_grouped

(290, 256)


Neighborhoods  African Restaurant   Airport  Airport Terminal  \
0            Airport Oaks            0.000000  0.142857          0.000000   
1                  Albany            0.000000  0.000000          0.000000   
2               Alfriston            0.000000  0.000000          0.000000   
3              Algies Bay            0.000000  0.000000          0.000000   
4                Anawhata            0.000000  0.000000          0.000000   
5                 Ararimu            0.000000  0.000000          0.000000   
6               Arch Hill            0.000000  0.000000          0.000000   
7                 Ardmore            0.000000  0.000000          0.000000   
8              Arkles Bay            0.000000  0.000000          0.000000   
9                Army Bay            0.000000  0.000000          0.000000   
10           Auckland CBD            0.000000  0.000000          0.000000   
11               Avondale            0.000000  0.000000          0.000000   
12                 Awhitu            0.000000  0.000000          0.000000   
13               Balmoral            0.000000  0.000000          0.000000   
14              Bayswater            0.000000  0.000000          0.055556   
15                Bayview            0.000000  0.000000          0.000000   
16            Beach Haven            0.000000  0.000000          0.000000   
17             Beachlands            0.000000  0.000000          0.000000   
18                Belmont            0.000000  0.000000          0.000000   
19         Bethells Beach            0.000000  0.000000          0.000000   
20              Big Omaha            0.000000  0.000000          0.000000   
21               Birkdale            0.000000  0.000000          0.000000   
22             Birkenhead            0.000000  0.000000          0.000000   
23              Blackpool            0.000000  0.000000          0.000000   
24         Blockhouse Bay            0.000000  0.000000          0.000000   
25                 Bombay            0.000000  0.000000          0.000000   
26           Botany Downs            0.000000  0.000000          0.000000   
27             Browns Bay            0.000000  0.000000          0.000000   
28               Buckland            0.000000  0.000000          0.000000   
29        Bucklands Beach            0.000000  0.000000          0.000000   
30               Burswood            0.000000  0.000000          0.000000   
31          Campbells Bay            0.000000  0.000000          0.000000   
32             Castor Bay            0.000000  0.000000          0.000000   
33           Chapel Downs            0.000000  0.000000          0.000000   
34              Chatswood            0.000000  0.000000          0.000000   
35             Cheltenham            0.000000  0.000000          0.000000   
36           Clarks Beach            0.000000  0.000000          0.000000   
37           Clendon Park            0.000000  0.000000          0.000000   
38               Clevedon            0.000000  0.000000          0.000000   
39            Clover Park            0.000000  0.000000          0.000000   
40             Cockle Bay            0.000000  0.000000          0.000000   
41          Conifer Grove            0.000000  0.000000          0.000000   
42             Cornwallis            0.000000  0.000000          0.000000   
43             Crown Hill            0.000000  0.000000          0.000000   
44             Dairy Flat            0.000000  0.000000          0.000000   
45              Dannemora            0.000000  0.000000          0.000000   
46              Devonport            0.000000  0.000000          0.000000   
47            Dome Forest            0.000000  0.000000          0.000000   
48            Dome Valley            0.000000  0.000000          0.000000   
49                  Drury            0.000000  0.000000          0.000000   
50            East Tamaki            0.000000  0.000000          0.000000   
51    Ea

In [30]:
len(ak_grouped[ak_grouped["Shopping Mall"] > 0])

123

#### Create a new DataFrame for Shopping Mall data only

In [31]:
ak_mall = ak_grouped[["Neighborhoods","Shopping Mall"]]

In [32]:
ak_mall

Neighborhoods  Shopping Mall
0            Airport Oaks       0.000000
1                  Albany       0.030303
2               Alfriston       0.000000
3              Algies Bay       0.010000
4                Anawhata       0.000000
5                 Ararimu       0.010000
6               Arch Hill       0.010000
7                 Ardmore       0.020000
8              Arkles Bay       0.000000
9                Army Bay       0.000000
10           Auckland CBD       0.010000
11               Avondale       0.027027
12                 Awhitu       0.010000
13               Balmoral       0.010000
14              Bayswater       0.000000
15                Bayview       0.083333
16            Beach Haven       0.000000
17             Beachlands       0.000000
18                Belmont       0.000000
19         Bethells Beach       0.000000
20              Big Omaha       0.010000
21               Birkdale       0.000000
22             Birkenhead       0.000000
23              Blackpool       0.000000
24         Blockhouse Bay       0.000000
25                 Bombay       0.010000
26           Botany Downs       0.035714
27             Browns Bay       0.000000
28               Buckland       0.000000
29        Bucklands Beach       0.000000
30               Burswood       0.020408
31          Campbells Bay       0.035714
32             Castor Bay       0.047619
33           Chapel Downs       0.020408
34              Chatswood       0.000000
35             Cheltenham       0.000000
36           Clarks Beach       0.000000
37           Clendon Park       0.000000
38               Clevedon       0.010000
39            Clover Park       0.027027
40             Cockle Bay       0.000000
41          Conifer Grove       0.000000
42             Cornwallis       0.000000
43             Crown Hill       0.024390
44             Dairy Flat       0.031746
45              Dannemora       0.023810
46              Devonport       0.000000
47            Dome Forest       0.000000
48            Dome Valley       0.000000
49                  Drury       0.022727
50            East Tamaki       0.000000
51    East Tamaki Heights       0.035714
52          Eastern Beach       0.000000
53           Eden Terrace       0.020000
54            Eden Valley       0.010000
55              Ellerslie       0.000000
56                  Epsom       0.000000
57       Fairview Heights       0.000000
58              Farm Cove       0.000000
59                 Favona       0.000000
60       Flamboro Heights       0.010000
61              Flat Bush       0.000000
62           Forrest Hill       0.020000
63           Freemans Bay       0.020000
64              Glen Eden       0.000000
65             Glen Innes       0.000000
66               Glendene       0.000000
67              Glendowie       0.000000
68              Glenfield       0.027778
69                 Glorit       0.010000
70              Golflands       0.018182
71       Goodwood Heights       0.032258
72                Grafton       0.010000
73             Greenhithe       0.000000
74              Greenlane       0.000000
75           Greenmeadows       0.000000
76      Greenwoods Corner       0.000000
77              Grey Lynn       0.020000
78           Gulf Harbour       0.020000
79          Half Moon Bay       0.000000
80        Hatfields Beach       0.038462
81                Hauraki       0.010000
82            Helensville       0.010000
83              Henderson       0.029412
84       Henderson Valley       0.000000
85          Herald Island       0.000000
86              Herne Bay       0.000000
87            Heron Point       0.034483
88               Highbury       0.000000
89          Highland Park       0.050000
90              Hillcrest       0.021277
91               Hillpark       0.055556
92           Hillsborough       0.000000
93            Hobsonville       0.000000
94                 Howick       0.000000
95                 Huapai       0.039216
96                   Huia       0.0

### 7. Cluster Neighborhoods
Run k-means to cluster the neighborhoods in Auckland into 3 clusters.

In [33]:
# set number of clusters
kclusters = 3

ak_clustering = ak_mall.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ak_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 1, 2, 2, 2, 2, 2, 1, 2, 2], dtype=int32)

In [34]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
ak_merged = ak_mall.copy()

# add clustering labels
ak_merged["Cluster Labels"] = kmeans.labels_

In [35]:
ak_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
ak_merged.head()

Neighborhood  Shopping Mall  Cluster Labels
0  Airport Oaks       0.000000               2
1        Albany       0.030303               1
2     Alfriston       0.000000               2
3    Algies Bay       0.010000               2
4      Anawhata       0.000000               2

In [36]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
ak_merged = ak_merged.join(ak_df.set_index("Neighborhood"), on="Neighborhood")

print(ak_merged.shape)
ak_merged.head() # check the last columns!

(290, 5)


Neighborhood  Shopping Mall  Cluster Labels   Latitude   Longitude
0  Airport Oaks       0.000000               2 -36.793589  174.618011
1        Albany       0.030303               1 -36.734272  174.699281
2     Alfriston       0.000000               2 -37.010493  174.940852
3    Algies Bay       0.010000               2 -36.848399  174.764388
4      Anawhata       0.000000               2 -36.922774  174.491364

In [37]:
# sort the results by Cluster Labels
print(ak_merged.shape)
ak_merged.sort_values(["Cluster Labels"], inplace=True)
ak_merged

(290, 5)


Neighborhood  Shopping Mall  Cluster Labels   Latitude  \
250        Tindalls Beach       0.068966               0 -36.966549   
184            Papatoetoe       0.062500               0 -36.976920   
179             Pakuranga       0.076923               0 -36.914538   
174                 Otara       0.166667               0 -36.962170   
15                Bayview       0.083333               0 -36.774527   
99                 Karaka       0.083333               0 -37.128200   
91               Hillpark       0.055556               0 -36.893196   
134            Meadowbank       0.062500               0 -36.869501   
171              Ormiston       0.095238               0 -36.962146   
190               Penrose       0.058824               0 -36.918134   
162              Onehunga       0.066667               0 -36.920599   
125         Manukau Heads       0.022727               1 -36.990685   
70              Golflands       0.018182               1 -36.923080   
124               Manukau       0.022727               1 -36.990685   
68              Glenfield       0.027778               1 -36.782597   
197              Ponsonby       0.020000               1 -36.850733   
71       Goodwood Heights       0.032258               1 -36.993773   
62           Forrest Hill       0.020000               1 -36.764423   
63           Freemans Bay       0.020000               1 -36.852879   
123                 Manly       0.022727               1 -36.711395   
244        Te Atatū South       0.029412               1 -36.869558   
245               Te Hana       0.031250               1 -36.899525   
246             Te Papapa       0.034483               1 -36.918200   
248           Three Kings       0.020833               1 -36.908233   
214           Saint Johns       0.031250               1 -36.868200   
53           Eden Terrace       0.020000               1 -36.864135   
130           Marlborough       0.031250               1 -36.778200   
77              Grey Lynn       0.020000               1 -36.861569   
230            Sunnyhills       0.040000               1 -36.901522   
232             Sunnyvale       0.043478               1 -36.898465   
106            Kohimarama       0.016393               1 -36.857260   
211             Royal Oak       0.032258               1 -36.910653   
113         Longford Park       0.020408               1 -36.913682   
220          Shelly Beach       0.020000               1 -36.839447   
207              Rosedale       0.021277               1 -36.746500   
97        Huntington Park       0.024390               1 -36.931362   
206             Riverhead       0.041667               1 -36.908184   
95                 Huapai       0.039216               1 -36.911677   
78           Gulf Harbour       0.020000               1 -36.844351   
224          Snells Beach       0.037037               1 -36.920952   
90              Hillcrest       0.021277               1 -36.793037   
89          Highland Park       0.050000               1 -36.904535   
226           Stanley Bay       0.021739               1 -36.770303   
87            Heron Point       0.034483               1 -36.919449   
167                Oranga       0.034483               1 -36.908200   
83              Henderson       0.029412               1 -36.879786   
51    East Tamaki Heights       0.035714               1 -36.942856   
80        Hatfields Beach       0.038462               1 -36.717908   
118          Mairangi Bay       0.023256               1 -36.741048   
192              Pinehill       0.028986               1 -36.731441   
144         Mount Roskill       0.045455               1 -36.916066   
26           Botany Downs       0.035714               1 -36.909453   
155            North Park       0.040816               1 -36.920491   
32             Castor Bay       0.047619               1 -36.760500   
31          Campbells Bay       0.035714               1 -36.749577   
30               Burswood       0.020

#### Let's visualize the resulting clusters

In [38]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ak_merged['Latitude'], ak_merged['Longitude'], ak_merged['Neighborhood'], ak_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [39]:
# save the map as HTML file
map_clusters.save('map_clusters1.html')

# 8. Examine Clusters to get a view of number of shopping malls

#### Cluster 0

In [40]:
ak_merged.loc[ak_merged['Cluster Labels'] == 0]

Neighborhood  Shopping Mall  Cluster Labels   Latitude   Longitude
250  Tindalls Beach       0.068966               0 -36.966549  174.880750
184      Papatoetoe       0.062500               0 -36.976920  174.855379
179       Pakuranga       0.076923               0 -36.914538  174.872924
174           Otara       0.166667               0 -36.962170  174.874850
15          Bayview       0.083333               0 -36.774527  174.709019
99           Karaka       0.083333               0 -37.128200  175.550210
91         Hillpark       0.055556               0 -36.893196  174.931355
134      Meadowbank       0.062500               0 -36.869501  174.829573
171        Ormiston       0.095238               0 -36.962146  174.893159
190         Penrose       0.058824               0 -36.918134  174.817623
162        Onehunga       0.066667               0 -36.920599  174.790655

#### Cluster 1

In [41]:
ak_merged.loc[ak_merged['Cluster Labels'] == 1]

Neighborhood  Shopping Mall  Cluster Labels   Latitude   Longitude
125        Manukau Heads       0.022727               1 -36.990685  174.876090
70             Golflands       0.018182               1 -36.923080  174.909470
124              Manukau       0.022727               1 -36.990685  174.876090
68             Glenfield       0.027778               1 -36.782597  174.721587
197             Ponsonby       0.020000               1 -36.850733  174.739223
71      Goodwood Heights       0.032258               1 -36.993773  174.897193
62          Forrest Hill       0.020000               1 -36.764423  174.747732
63          Freemans Bay       0.020000               1 -36.852879  174.750353
123                Manly       0.022727               1 -36.711395  174.750475
244       Te Atatū South       0.029412               1 -36.869558  174.647331
245              Te Hana       0.031250               1 -36.899525  174.858177
246            Te Papapa       0.034483               1 -36.918200  174.800190
248          Three Kings       0.020833               1 -36.908233  174.757223
214          Saint Johns       0.031250               1 -36.868200  174.840190
53          Eden Terrace       0.020000               1 -36.864135  174.757433
130          Marlborough       0.031250               1 -36.778200  174.720190
77             Grey Lynn       0.020000               1 -36.861569  174.739555
230           Sunnyhills       0.040000               1 -36.901522  174.885906
232            Sunnyvale       0.043478               1 -36.898465  174.636527
106           Kohimarama       0.016393               1 -36.857260  174.840978
211            Royal Oak       0.032258               1 -36.910653  174.772330
113        Longford Park       0.020408               1 -36.913682  174.837019
220         Shelly Beach       0.020000               1 -36.839447  174.741570
207             Rosedale       0.021277               1 -36.746500  174.715221
97       Huntington Park       0.024390               1 -36.931362  174.906662
206            Riverhead       0.041667               1 -36.908184  174.865732
95                Huapai       0.039216               1 -36.911677  174.785139
78          Gulf Harbour       0.020000               1 -36.844351  174.749958
224         Snells Beach       0.037037               1 -36.920952  174.875965
90             Hillcrest       0.021277               1 -36.793037  174.735203
89         Highland Park       0.050000               1 -36.904535  174.908448
226          Stanley Bay       0.021739               1 -36.770303  174.756699
87           Heron Point       0.034483               1 -36.919449  174.884300
167               Oranga       0.034483               1 -36.908200  174.790190
83             Henderson       0.029412               1 -36.879786  174.622935
51   East Tamaki Heights       0.035714               1 -36.942856  174.925778
80       Hatfields Beach       0.038462               1 -36.717908  174.695455
118         Mairangi Bay       0.023256               1 -36.741048  174.747546
192             Pinehill       0.028986               1 -36.731441  174.723566
144        Mount Roskill       0.045455               1 -36.916066  174.736536
26          Botany Downs       0.035714               1 -36.909453  174.917068
155           North Park       0.040816               1 -36.920491  174.919753
32            Castor Bay       0.047619               1 -36.760500  174.761817
31         Campbells Bay       0.035714               1 -36.749577  174.756271
30              Burswood       0.020408               1 -36.924400  174.897167
182              Panmure       0.027778               1 -36.897420  174.859564
181           Palm Beach       0.052632               1 -36.913903  174.869455
279             Westgate       0.040000               1 -36.821520  174.611870
150             New Lynn       0.020000               1 -36.913037  174.678813
267              Waitoki       0.035714               1 -36.89

#### Cluster 2

In [42]:
ak_merged.loc[ak_merged['Cluster Labels'] == 2]

Neighborhood  Shopping Mall  Cluster Labels   Latitude  \
176              Owairaka       0.000000               2 -36.888200   
208              Rosehill       0.010000               2 -36.848399   
210         Royal Heights       0.000000               2 -36.832691   
177               Paerata       0.000000               2 -36.887049   
173               Otahuhu       0.000000               2 -36.943905   
205               Remuera       0.000000               2 -36.877404   
178            Pahurehure       0.000000               2 -37.058200   
172                Ostend       0.000000               2 -36.798200   
209          Rothesay Bay       0.000000               2 -36.724163   
191                  Piha       0.000000               2 -36.944077   
203              Red Hill       0.000000               2 -36.848190   
193       Point Chevalier       0.000000               2 -36.866297   
189             Patumahoe       0.010000               2 -36.848399   
194         Point England       0.000000               2 -36.883958   
188               Parnell       0.010000               2 -36.853980   
187            Paremoremo       0.000000               2 -36.766670   
195           Point Wells       0.000000               2 -36.318190   
186                 Parau       0.000000               2 -36.966670   
196                Pollok       0.010000               2 -36.848399   
185               Parakai       0.000000               2 -37.148200   
198           Port Albert       0.000000               2 -36.824426   
183              Paparimu       0.010000               2 -36.848399   
199                 Puhoi       0.010000               2 -36.848399   
200         Randwick Park       0.000000               2 -37.023824   
201                 Ranui       0.000000               2 -36.865026   
202             Red Beach       0.000000               2 -36.713880   
204               Redvale       0.000000               2 -36.683330   
212              Runciman       0.010000               2 -36.848399   
229           Stonefields       0.000000               2 -36.887335   
215       Saint Marys Bay       0.014085               2 -36.838200   
257      Unsworth Heights       0.000000               2 -36.757412   
258       Wai o Taiki Bay       0.000000               2 -36.868200   
259                Waiake       0.000000               2 -36.706590   
260             Waiatarua       0.000000               2 -36.934048   
261              Waiau Pa       0.000000               2 -36.693181   
262             Waikowhai       0.000000               2 -36.928200   
263      Waimahia Landing       0.000000               2 -37.043495   
264              Waimauku       0.010000               2 -36.848399   
265                Wainui       0.000000               2 -36.861317   
266         Wairau Valley       0.015152               2 -36.775694   
268                Waiuku       0.010000               2 -36.848399   
269               Waiwera       0.000000               2 -36.550000   
256        Tuscany Estate       0.000000               2 -36.843709   
270             Warkworth       0.000000               2 -36.428190   
273          Wattle Downs       0.000000               2 -37.047450   
276       Western Heights       0.000000               2 -36.878200   
277       Western Springs       0.000000               2 -36.863106   
278             Westfield       0.000000               2 -36.950000   
280              Westlake       0.010000               2 -36.785000   
281              Westmere       0.000000               2 -37.568210   
282              Weymouth       0.000000               2 -37.048200   
283          Whangaparaoa       0.000000               2 -36.233330   
284            Whangateau       0.000000               2 -36.318190   
285             Wharehine       0.000000               2 -36.278190   
286             Whenuapai       0.000000               2 -36.787780   
287              Whitford       0.000

### Observations:

Most of the shopping malls are concentrated in the central area of Auckland city, with the highest number in cluster 0 and moderate number in cluster 1. On the other hand, cluster 2 has very low number or no shopping mall in the neighborhoods. This represents a great opportunity and high potential areas to open new shopping malls as there is very little to no competition from existing malls. Meanwhile, shopping malls in cluster 0 are likely suffering from intense competition due to oversupply and high concentration of shopping malls. From another perspective, this also shows that the oversupply of shopping malls mostly happened in the central area of the city, with the suburb area still have very few shopping malls. Therefore, this project recommends property developers to capitalize on these findings to open new shopping malls in neighborhoods in cluster 2 with little to no competition. Property developers with unique selling propositions to stand out from the competition can also open new shopping malls in neighborhoods in cluster 1 with moderate competition. Lastly, property developers are advised to avoid neighborhoods in cluster 0 which already have high concentration of shopping malls and suffering from intense competition.